In [1]:
import warnings
import itertools
import pandas
import math
import sys
import os
import numpy as np
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

In [30]:
# realAWSCloudwatch/grok_asg_anomaly.csv low

result_file1 = "../results/LSTMCNnet/realAWSCloudwatch/LSTMCNnet_grok_asg_anomaly.csv"
result_file2 = "../results/numenta/realAWSCloudwatch/numenta_grok_asg_anomaly.csv"

# realAWSCloudwatch/iio_us-east-1_i-a2eb1cd9_NetworkIn.csv high

# result_file1 = "../results/LSTMCNnet/realAWSCloudwatch/LSTMCNnet_iio_us-east-1_i-a2eb1cd9_NetworkIn.csv"
# result_file2 = "../results/numenta/realAWSCloudwatch/numenta_iio_us-east-1_i-a2eb1cd9_NetworkIn.csv"

detector_name1 = 'LSTMCNnet'
detector_name2 = 'numenta'


threshold1 = 0.5
threshold2 = 0.5126953125

extra_colomn1 = 'DTW_similarity'
extra_colomn2 = 'raw_score'

# TSA_ARMA  0.9749755859375003  prediction
# LSTMCNnet  0.5  DTW_similarity
# numenta  0.5126953125  raw_score

color1 = 'red'
color2 = 'blue'

result_files = [result_file1,result_file2]
detector_names = [detector_name1,detector_name2]
thresholds = [threshold1,threshold2]
extra_colomns = [extra_colomn1,extra_colomn2]
anomaly_marker_colors = [color1,color2]

detector_profile='S(t)_standard'

In [34]:
#GENERATES 2 GRAPHS
def compare_detectors(result_files, thresholds, detector_names, extra_colomns, anomaly_marker_colors):
    
    no_of_detecors = len(result_files)
    DataFrame = pandas.read_csv(result_files[0])
    x = np.array(DataFrame['timestamp'])
    
    trace_values = [{} for _ in range(no_of_detecors)] 
    trace_anomalies = [{} for _ in range(no_of_detecors)] 
#     trace_anolamy_labels = [{} for _ in range(no_of_detecors)] 

    trace_scaled_anolamy_labels = [{} for _ in range(no_of_detecors)] 
    trace_scores = [{} for _ in range(no_of_detecors)]
#     trace_scaled_values = [{} for _ in range(no_of_detecors)]
    trace_extra_colomns = [{} for _ in range(no_of_detecors)]
    
    
    anomalies = [[] for _ in range(no_of_detecors)]
    
    value_traces = []
    score_traces = []
    
    for i in range(0,len(result_files)):
        print("comparing results in file : "+ result_files[i])
        DataFrame = pandas.read_csv(result_files[i])
        
        anomalies[i] = np.zeros(len(DataFrame['anomaly_score']))
        
        for j in range(0, len(DataFrame['anomaly_score'])):
            if DataFrame['anomaly_score'][j] >= thresholds[i]:
                anomalies[i][j] = 0.9
            else:
                anomalies[i][j] = float('nan')
        
        
        value = np.array(DataFrame['value'])
        max_value = np.max(value)
        trace_values[i] = {"x": x, 
                           "y": value,
                            "mode": 'lines',
                            "name": 'value|'+detector_names[i]}
        
        label = np.array(DataFrame['label'])
        trace_scaled_anolamy_labels[i] = {"x": x, 
                           "y": label*max_value,
                            "mode": 'lines',
                            "name": 'scaled label|' + detector_names[i]}
        trace_scores[i] = {"x": x, 
                           "y": DataFrame[detector_profile],
                            "mode": 'lines',
                            "name": 'score|' + detector_names[i],
                            "line":{"color": anomaly_marker_colors[i]}
                          }
        trace_anomalies[i] = {"x": x, 
                           "y": anomalies[i],
                            "mode": 'markers',
                            "name": 'anomaly|' + detector_names[i],
                            "marker": {
                                "size": 5,
                                "color": anomaly_marker_colors[i],
                                "line": {"width": 1}
                                    }
                                  }
        
        value_traces.append(trace_values[i])
        value_traces.append(trace_scaled_anolamy_labels[i])
        
        score_traces.append(trace_anomalies[i])
        score_traces.append(trace_scores[i])
        
        if extra_colomns[i] != '':
            extra_colomn = np.array(DataFrame[extra_colomns[i]])
            max_extra_colomn = np.max(extra_colomn)
            trace_extra_colomns[i] = {"x": x, 
                           "y": extra_colomn/max_extra_colomn,
                            "mode": 'lines',
                            "name": 'scaled '+extra_colomns[i]+'|'+detector_names[i]}
            
            score_traces.append(trace_extra_colomns[i])
    
    
    trace_scaled_values = {"x": x, 
                           "y": value/max_value,
                            "mode": 'lines',
                            "name": 'scaled value'}
    
    trace_anolamy_labels = {"x": x, 
                           "y": label,
                            "mode": 'lines',
                            "name": 'label'}
    
    score_traces.append(trace_scaled_values)
    score_traces.append(trace_anolamy_labels)
    
    layout = dict(title = "Values",
                  xaxis = dict(title = 'X'),
                  yaxis = dict(title = 'Value')
                 )
    fig = dict(data=value_traces, layout=layout)
    iplot(fig)

    layout = dict(title = "Values",
                  xaxis = dict(title = 'X'),
                  yaxis = dict(title = 'Value')
                 )
    fig = dict(data=score_traces, layout=layout)
    iplot(fig)


# GENERATES BELOW TABLE
def check_data_point(score):
    if score > 0:
        return 'TP'
    elif score == -0.11:
        return 'FP'
    elif score == -1:
        return 'FN'
    return ''

def color_cells(val):
    if val == 'TP':
        color = 'lightgreen'
    elif val == 'FP':
        color = 'yellow'
    elif val == 'FN':
        color = 'red'
    else:
        color = 'black'
    return 'color: %s' % color

def results_table(result_files, detector_names,output_csv_file):
    scores = [[] for _ in range(len(detector_names))]
    results = [[] for _ in range(len(detector_names))]
    tmp_results = ['' for _ in range(len(detector_names))]
    
    DataFrame = pandas.read_csv(result_files[0])
    x = np.array(DataFrame['timestamp'])
    
    for i in range(0,len(result_files)):
        DataFrame = pandas.read_csv(result_files[i])
        scores[i] = np.array(DataFrame[detector_profile])
    
    time = []
    for i in range(0,len(x)):
        got_result = False
        for j in range(0,len(detector_names)):
            tmp_results[j] = check_data_point(scores[j][i])
            if tmp_results[j] != '':
                got_result = True
        if got_result:
            time.append(x[i])
            for j in range(0,len(detector_names)):
                results[j].append(tmp_results[j])
    
    output_colomns = {}
    for i in range(0,len(detector_names)):
        output_colomns[detector_names[i]] = results[i]
    output_csv_DataFrame =  pandas.DataFrame(output_colomns,
                                index=time)
    
    output_csv_DataFrame.to_csv(output_csv_file)
    print("Done writing " + output_csv_file)
    
    return output_csv_DataFrame.style.set_properties(**{'background-color': 'black',
                           'border-color': 'white',
                            'border-style': 'solid'}).applymap(color_cells)
    

In [32]:
compare_detectors(result_files, thresholds, detector_names, extra_colomns, anomaly_marker_colors)

comparing results in file : ../results/LSTMCNnet/realAWSCloudwatch/LSTMCNnet_grok_asg_anomaly.csv
comparing results in file : ../results/numenta/realAWSCloudwatch/numenta_grok_asg_anomaly.csv


In [35]:
output_csv_file = '../results/result_summary.csv'
results_table(result_files, detector_names,output_csv_file)

Done writing ../results/result_summary.csv
